# Examples of market data queries

You can execute each of these queries either running each cell one after another, or copying the SQL and executing on the QuestDB Web Console at http://localhost:9000

In [11]:
import psycopg as pg

def exec_sql(query):
    # Create the connection string using the environment variables or defaults
    conn_str = f'user=admin password=quest host=host.docker.internal port=8812 dbname=qdb'
    with pg.connect(conn_str) as connection:
        with connection.cursor() as cur:
            #Query the database and obtain data as Python objects.    
            cur.execute(query)
            records = cur.fetchall()
            for row in records:
                print(row)

    # the connection is now closed

## Query Name: Most recent price of BTC and ETH

```sql
/* Find the latest value available for each symbol. */
```


In [16]:
query="""
SELECT * FROM trades
WHERE symbol in ('BTC-USDT', 'ETH-USDT')
LATEST ON timestamp PARTITION BY symbol;
"""

exec_sql(query)

('BTC-USDT', 'buy', 61178.051250000004, 0.01803645625, datetime.datetime(2025, 3, 31, 14, 51, 7, 933156))
('ETH-USDT', 'sell', 3343.255925925926, 0.285525075925, datetime.datetime(2025, 3, 31, 14, 51, 8, 298467))


## Query Name: Bar chart (OHLC) downsampled with a 15 minutes interval

```sql
/* Aggregations for the BTC-USDT for today downsampled in 15-minute intervals.
 We use the SQL extension SAMPLE BY to aggregate data at regular intervals. QuestDB
 ingests live market data from the OKX API. */
```

In [17]:
query=""" 
SELECT
    timestamp, symbol,
    first(price) AS open,
    last(price) AS close,
    min(price),
    max(price),
    sum(amount) AS volume
FROM trades
WHERE symbol = 'BTC-USDT' AND timestamp IN today()
SAMPLE BY 15m;
"""

exec_sql(query)

(datetime.datetime(2025, 3, 31, 11, 0), 'BTC-USDT', 82166.5, 82130.0, 82014.0, 82188.0, 33.80812163999989)
(datetime.datetime(2025, 3, 31, 11, 15), 'BTC-USDT', 82128.1, 81972.2, 81972.1, 82237.0, 32.273324339999846)
(datetime.datetime(2025, 3, 31, 11, 30), 'BTC-USDT', 81972.2, 82042.6, 81900.3, 82060.7, 31.799217559999672)
(datetime.datetime(2025, 3, 31, 11, 45), 'BTC-USDT', 82042.6, 82223.5, 82031.5, 82230.1, 24.487800579999952)
(datetime.datetime(2025, 3, 31, 14, 30), 'BTC-USDT', 83093.6, 83173.0, 83072.1, 83366.5, 50.943872010001314)
(datetime.datetime(2025, 3, 31, 14, 45), 'BTC-USDT', 83173.0, 61178.051250000004, 61135.78, 83262.0, 12.766094652902495)


## Query Name: VWAP Bitcoin price, cumulative with a 10 minute interval for one day

```sql
/* Calculates the weighted average for BTC-USDT for yesterday, cumulative in 10-minute intervals.
 We use the SQL extension SAMPLE BY to aggregate data at regular intervals.
 Then we use window functions to calculate cumulative values and get the VWAP
QuestDB ingests live market data from the OKX API */
```

In [18]:
query="""
WITH btc_usdt AS (
    SELECT
          timestamp,  symbol,
          SUM(amount) AS volume,
          SUM(price * amount) AS traded_value
     FROM trades
     WHERE timestamp IN today()
     AND symbol = 'BTC-USDT'
     SAMPLE BY 10m
), cumulative AS (
     SELECT timestamp, symbol,
           SUM(traded_value)
                OVER (ORDER BY timestamp) AS cumulative_value,
           SUM(volume)
                OVER (ORDER BY timestamp) AS cumulative_volume
     FROM btc_usdt
)
SELECT *, cumulative_value/cumulative_volume AS vwap FROM cumulative;
"""

exec_sql(query)

(datetime.datetime(2025, 3, 31, 11, 0), 'BTC-USDT', 1490825.1843714803, 18.16078819999992, 82090.33484413891)
(datetime.datetime(2025, 3, 31, 11, 10), 'BTC-USDT', 3231336.3223621068, 39.35535715999991, 82106.64457255593)
(datetime.datetime(2025, 3, 31, 11, 20), 'BTC-USDT', 5424103.483093946, 66.08144597999978, 82082.09434060517)
(datetime.datetime(2025, 3, 31, 11, 30), 'BTC-USDT', 7499748.350599946, 91.40249783999958, 82051.8971344556)
(datetime.datetime(2025, 3, 31, 11, 40), 'BTC-USDT', 9392504.864852592, 114.46525052999948, 82055.51310431081)
(datetime.datetime(2025, 3, 31, 11, 50), 'BTC-USDT', 10042114.254398076, 122.36846411999947, 82064.5607233443)
(datetime.datetime(2025, 3, 31, 14, 30), 'BTC-USDT', 11097483.559782868, 135.05381948999943, 82170.82346645238)
(datetime.datetime(2025, 3, 31, 14, 40), 'BTC-USDT', 15200821.338777905, 185.22826578869245, 82065.343936864)
(datetime.datetime(2025, 3, 31, 14, 50), 'BTC-USDT', 15252828.698219, 186.07843078290324, 81969.89105101814)


## Query Name: Hourly returns (%) of BTC

```sql
/* Calculates the hourly returns in % for BTC-USDT for the last 30 days.
 We use SAMPLE BY to aggregate the data at regular intervals - in this case daily.
 The previous value is obtained with the first_value() window function */
```

In [20]:
query=""" 
select timestamp, round(100*(last_price - prev_price) / prev_price, 2) as return_pct
from
(
  select timestamp, last_price, first_value(last_price) over (rows between 1 preceding and 1 preceding) as prev_price
  from
  (
    SELECT timestamp, last(price) last_price
    FROM trades
    WHERE symbol = 'BTC-USDT'
    and timestamp > dateadd('d', -30, now())
    SAMPLE BY 1h
  )
)
where prev_price is not null;
"""

exec_sql(query)

(datetime.datetime(2025, 3, 28, 16, 0), 0.05)
(datetime.datetime(2025, 3, 28, 17, 0), -0.41000000000000003)
(datetime.datetime(2025, 3, 31, 11, 0), -1.86)
(datetime.datetime(2025, 3, 31, 14, 0), -25.6)


## Query Name: Find gaps in your trading data

```sql
/* Aggregates data in 1 minute intervals, interpolating with empty values any gaps where we do not
 have sell operations for each tracked symbol. We use the SAMPLE BY keyword to aggregate data per minute,
using the FILL(NULL) keyword to instruct QuestDB to output an empty column for any gaps. We could have also used
 FILL(LINEAR) or FILL(PREV) for different interpolation strategies.
 Note we are using DECLARE to define the SAMPLE interval and the time_range. You could try
 values such as @sample_interval := 30s, @time_range := yesterday(),
 or @time_range := INTERVAL( interval_start( yesterday ()), now() ) */
```

In [22]:
query="""DECLARE
  @sample_interval := 1m,
  @time_range := today()
SELECT
   timestamp, symbol, side, sum(amount) as volume
 FROM trades
 WHERE side = 'sell' AND timestamp IN @time_range
 SAMPLE BY @sample_interval FILL(NULL);
"""
exec_sql(query)

(datetime.datetime(2025, 3, 31, 11, 3), 'BTC-USDT', 'sell', 0.4584842600000001)
(datetime.datetime(2025, 3, 31, 11, 3), 'ETH-USDT', 'sell', 12.532128999999998)
(datetime.datetime(2025, 3, 31, 11, 3), 'ADA-USDT', 'sell', 830.0)
(datetime.datetime(2025, 3, 31, 11, 3), 'ETH-BTC', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'SOL-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'DOGE-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'SHIB-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'BTC-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'ADA-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'DOT-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'ETH-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'AVAX-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'UNI-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'MATIC-USD', 'sell', None)
(datetime.datetime(2025, 3, 31, 11, 3), 'LTC-USD', 's

## Query Name: 30d and 15d Moving Average

```sql
/* Calculates the rolling moving average of BTC-USDT using Window Functions */
```
    

In [24]:
query="""
SELECT timestamp time, symbol, price as priceBtc,
       avg(price) over (PARTITION BY symbol ORDER BY timestamp RANGE between 15 minutes PRECEDING AND CURRENT ROW) moving_avg_15_minutes,
       avg(price) over (PARTITION BY symbol ORDER BY timestamp RANGE between 30 minutes PRECEDING AND CURRENT ROW) moving_avg_30_minutes
FROM trades
WHERE timestamp > dateadd('M', -1, now())
AND symbol = 'BTC-USDT';
"""
exec_sql(query)

(datetime.datetime(2025, 3, 28, 15, 56, 9, 907000), 'BTC-USDT', 84168.7, 84168.7, 84168.7)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 60000), 'BTC-USDT', 84168.6, 84168.65, 84168.65)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 115000), 'BTC-USDT', 84167.0, 84168.09999999999, 84168.09999999999)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 115000), 'BTC-USDT', 84163.2, 84166.875, 84166.875)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 246000), 'BTC-USDT', 84160.0, 84165.5, 84165.5)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 246000), 'BTC-USDT', 84158.5, 84164.33333333333, 84164.33333333333)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 588000), 'BTC-USDT', 84158.1, 84163.44285714286, 84163.44285714286)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 732000), 'BTC-USDT', 84158.1, 84162.775, 84162.775)
(datetime.datetime(2025, 3, 28, 15, 56, 11, 164000), 'BTC-USDT', 84158.0, 84162.24444444444, 84162.24444444444)
(datetime.datetime(2025, 3, 28, 15, 56, 12, 700999), 'BTC-USDT', 84158.0, 84161.8199

## Query Name: Implied BTC-ETH exchange rate

```sql
/* This query calculates the implied BTC-ETH exchange rate using BTC-USDT and
 ETH-USDT quotes from the OKX API.
 We use ASOF JOIN, a fuzzy timestamp based lookup from one table to another. */
```

In [25]:
query="""
WITH btc AS (
    SELECT timestamp, price
    FROM trades
    WHERE symbol = 'BTC-USDT' AND timestamp > dateadd('d', -30, now())
),
eth AS (
    SELECT timestamp, price
    FROM trades
    WHERE symbol = 'ETH-USDT' and timestamp > dateadd('d', -30, now())
)
SELECT
    btc.timestamp btc_time,
    btc.price btc_price,
    eth.price eth_price,
    round(btc.price/eth.price, 3) btc_to_eth_ratio
FROM btc
ASOF JOIN eth;
"""
exec_sql(query)

(datetime.datetime(2025, 3, 28, 15, 56, 9, 907000), 84168.7, 1876.5, 44.854)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 60000), 84168.6, 1876.41, 44.856)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 115000), 84167.0, 1876.41, 44.855000000000004)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 115000), 84163.2, 1876.41, 44.853)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 246000), 84160.0, 1876.41, 44.852000000000004)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 246000), 84158.5, 1876.41, 44.851)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 588000), 84158.1, 1876.41, 44.851)
(datetime.datetime(2025, 3, 28, 15, 56, 10, 732000), 84158.1, 1876.41, 44.851)
(datetime.datetime(2025, 3, 28, 15, 56, 11, 164000), 84158.0, 1876.41, 44.851)
(datetime.datetime(2025, 3, 28, 15, 56, 12, 700999), 84158.0, 1876.27, 44.854)
(datetime.datetime(2025, 3, 28, 15, 56, 12, 700999), 84154.0, 1876.27, 44.852000000000004)
(datetime.datetime(2025, 3, 28, 15, 56, 12, 700999), 84153.6, 1876.27, 44.852000000000004)
(dateti

## Query Name: Most recent sell event for each buy

```sql
/* This query finds each buy event, and joins with the most
 recent sell event for the same symbol.
 */
```
 

In [32]:
query="""
WITH trade_buys AS  (
 SELECT timestamp, symbol, price, side
 FROM trades
 WHERE side = 'buy' 
 ), trade_sells AS  (
         SELECT timestamp, symbol, price, side
 FROM trades
 WHERE side = 'sell' 
 )
 SELECT * from trade_buys ASOF JOIN trade_sells ON (symbol) limit -30;
"""
exec_sql(query)

(datetime.datetime(2025, 3, 31, 14, 51, 7, 930309), 'BTC-USDT', 61178.051250000004, 'buy', datetime.datetime(2025, 3, 31, 14, 51, 6, 796255), 'BTC-USDT', 61186.195, 'sell')
(datetime.datetime(2025, 3, 31, 14, 51, 7, 933156), 'BTC-USDT', 61178.051250000004, 'buy', datetime.datetime(2025, 3, 31, 14, 51, 6, 796255), 'BTC-USDT', 61186.195, 'sell')
(datetime.datetime(2025, 3, 31, 14, 51, 7, 981256), 'UNI-USD', 11.128666666666, 'buy', datetime.datetime(2025, 3, 31, 14, 51, 7, 416208), 'UNI-USD', 11.129333333333, 'sell')
(datetime.datetime(2025, 3, 31, 14, 51, 7, 984656), 'UNI-USD', 11.128666666666, 'buy', datetime.datetime(2025, 3, 31, 14, 51, 7, 416208), 'UNI-USD', 11.129333333333, 'sell')
(datetime.datetime(2025, 3, 31, 14, 51, 8, 35449), 'USDT-USDC', 1.00055, 'buy', datetime.datetime(2025, 3, 31, 14, 49, 18, 628415), 'USDT-USDC', 1.0005, 'sell')
(datetime.datetime(2025, 3, 31, 14, 51, 8, 37786), 'USDT-USDC', 1.00055, 'buy', datetime.datetime(2025, 3, 31, 14, 49, 18, 628415), 'USDT-USDC', 

## Query Name: Significant prices only

```sql
/* Select only rows with different price than previous row for same symbol and side.
 We use the LAG function to get the value from the previous row for the same symbol and side */
```

In [31]:
query=""" 
WITH trade_and_previous AS (
SELECT timestamp, symbol, side, price,
       LAG(price) OVER(PARTITION BY symbol, side ORDER BY timestamp) as prev_price
FROM trades
WHERE timestamp IN today()
)
select * from trade_and_previous where price <> prev_price limit -20;
"""
exec_sql(query)

(datetime.datetime(2025, 3, 31, 14, 51, 7, 981256), 'UNI-USD', 'buy', 11.128666666666, 11.14319047619)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 35449), 'USDT-USDC', 'buy', 1.00055, 1.0005)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 145481), 'DOGE-BTC', 'sell', 1.914e-06, 1.9157142857142857e-06)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 247568), 'ADA-USD', 'sell', 0.6555, 0.655656249999)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 298376), 'ETH-USDT', 'sell', 3343.255925925926, 3339.537999999999)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 349225), 'SOL-USD', 'buy', 126.482857142857, 126.236428571428)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 400563), 'ETH-BTC', 'buy', 0.05465, 0.054595)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 451527), 'SOL-BTC', 'buy', 0.00206526428571, 0.00206323333333)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 502186), 'SHIB-USD', 'buy', 1.2570000000000003e-05, 1.2573599999999994e-05)
(datetime.datetime(2025, 3, 31, 14, 51, 8, 553740), 'MATIC-USD', 'buy', 1.004

## Query Name: The weighted mid price for bids and asks

```sql
/* The weighted mid price for bids and asks.
We first separate our trades table into bids and
asks depending on side, and then we aggregate at
1 second intervals. Then we use ASOF JOIN to
get the closest ask for the bid, and use the
wmid function  */
```

In [34]:
query="""
WITH bids AS (
SELECT timestamp AS bid_ts, symbol,
   amount AS bid_size,
   avg(price*amount) AS bid_price
 FROM trades WHERE side = 'buy'  
 SAMPLE BY 1s
), asks AS  (
 SELECT timestamp AS ask_ts, symbol,
   amount AS ask_size,
   avg(price*amount) AS ask_price
 FROM trades  WHERE side = 'sell'
 SAMPLE BY 1s
)
SELECT bid_ts, bids.symbol, bid_size, bid_price,
wmid(bid_price, bid_size, ask_price, ask_size) AS weighted_mid_price,
ask_price, ask_size,
 FROM bids ASOF JOIN asks ON (symbol) where ask_price is not null LIMIT -30;
"""
exec_sql(query)

(datetime.datetime(2025, 3, 31, 14, 51, 6), 'SOL-ETH', 2.141666666666, 0.0809549999999748, 2.1017797958479214, 0.14939001999999998, 3.9626)
(datetime.datetime(2025, 3, 31, 14, 51, 6), 'BTC-USD', 0.0358936282795, 2197.1513185645604, 1289.1625161930408, 1289.1748731486896, 0.0210608492)
(datetime.datetime(2025, 3, 31, 14, 51, 6), 'XLM-USD', 624.994311297241, 76.50999326048586, 576.0936613560929, 92.56205087227787, 756.533917317499)
(datetime.datetime(2025, 3, 31, 14, 51, 7), 'ADA-USDT', 330.85, 217.03760000000003, 231.72079453394167, 136.4796125, 208.525)
(datetime.datetime(2025, 3, 31, 14, 51, 7), 'ETH-USD', 0.314517456296, 1051.2728503501787, 1313.9597044042685, 1314.4511711920088, 0.393306880681)
(datetime.datetime(2025, 3, 31, 14, 51, 7), 'ETH-USDT', 0.320654712, 1070.9362884053119, 798.6193724271208, 798.7976727781682, 0.239194065999)
(datetime.datetime(2025, 3, 31, 14, 51, 7), 'ETH-BTC', 0.43155, 0.02356047225, 0.424619240248971, 0.066474408, 1.21748)
(datetime.datetime(2025, 3, 31

## Query Name: Query trade data from a parquet file

```sql
/*
This query reads from a sample parquet file that is now packaged with QuestDB as of
version 8.1.1. It demonstrates how one can seamlessly integrate data in open
formats with the QuestDB query engine.
*/
```

In [36]:
query="""
select * from read_parquet('trades.parquet') limit 50;
"""
exec_sql(query)

('BTC-USD', 'buy', 62755.6, 0.00043367, datetime.datetime(2024, 7, 1, 0, 46, 39, 754075))
('BTC-USD', 'buy', 63411.53, 4.98e-06, datetime.datetime(2024, 7, 1, 1, 12, 6, 173382))
('BTC-USD', 'buy', 63448.34, 4.042e-05, datetime.datetime(2024, 7, 1, 1, 37, 32, 450063))
('BTC-USD', 'buy', 63704.61, 0.0691299, datetime.datetime(2024, 7, 1, 2, 4, 43, 670727))
('BTC-USD', 'sell', 63483.13, 0.00610517, datetime.datetime(2024, 7, 1, 2, 20, 50, 726753))
('BTC-USD', 'buy', 63289.68, 1.994e-05, datetime.datetime(2024, 7, 1, 2, 49, 50, 634694))
('BTC-USD', 'sell', 63337.39, 4.98e-06, datetime.datetime(2024, 7, 1, 3, 40, 21, 374128))
('BTC-USD', 'buy', 63204.36, 0.06, datetime.datetime(2024, 7, 1, 4, 40, 26, 744591))
('BTC-USD', 'sell', 63368.4, 0.04822351, datetime.datetime(2024, 7, 1, 6, 4, 30, 16011))
('BTC-USD', 'sell', 63303.38, 0.00082433, datetime.datetime(2024, 7, 1, 7, 19, 16, 273900))
('BTC-USD', 'buy', 63007.6, 0.23806652, datetime.datetime(2024, 7, 1, 8, 32, 24, 849148))
('BTC-USD', 'bu

## Query Name: Query trade data from parquet using time-series extensions

```sql
/*
This query reads from a sample parquet file that is now packaged with QuestDB as of
version 8.1.1. It demonstrates how one can assign the designated timestamp
when querying over an external table, so functions like SAMPLE BY can be used*/
```

In [37]:
query="""
select timestamp, avg(price) from (read_parquet('trades.parquet') timestamp(timestamp)) sample by 15m;
"""
exec_sql(query)

(datetime.datetime(2024, 7, 1, 0, 45), 62755.6)
(datetime.datetime(2024, 7, 1, 1, 0), 63411.53)
(datetime.datetime(2024, 7, 1, 1, 30), 63448.34)
(datetime.datetime(2024, 7, 1, 2, 0), 63704.61)
(datetime.datetime(2024, 7, 1, 2, 15), 63483.13)
(datetime.datetime(2024, 7, 1, 2, 45), 63289.68)
(datetime.datetime(2024, 7, 1, 3, 30), 63337.39)
(datetime.datetime(2024, 7, 1, 4, 30), 63204.36)
(datetime.datetime(2024, 7, 1, 6, 0), 63368.4)
(datetime.datetime(2024, 7, 1, 7, 15), 63303.38)
(datetime.datetime(2024, 7, 1, 8, 30), 63007.6)
(datetime.datetime(2024, 7, 1, 9, 30), 62817.73)
(datetime.datetime(2024, 7, 1, 10, 45), 62745.05)
(datetime.datetime(2024, 7, 1, 11, 45), 62531.78)
(datetime.datetime(2024, 7, 1, 12, 45), 62800.04)
(datetime.datetime(2024, 7, 1, 13, 30), 62811.42)
(datetime.datetime(2024, 7, 1, 14, 0), 62683.29)
(datetime.datetime(2024, 7, 1, 14, 15), 62718.98)
(datetime.datetime(2024, 7, 1, 14, 45), 62727.04)
(datetime.datetime(2024, 7, 1, 15, 15), 62764.77)
(datetime.datetime(

## Query Name: Find price trend boundaries

```sql
/* Find trades where an upwards or downwards trend changed direction.
   We use LAG to get the previous value for each row, then we use
   CASE to output 1, 0, or NULL depending on the comparison with
   the previous row, then we use LAG with IGNORE NULLS, so we
   are ignoring all the values that had no changes in the trend,
   and we can finally show only the rows where there was a trend
   change, together with the difference from the previous price.
*/
```

In [39]:

query="""
WITH trade_and_previous AS (
SELECT timestamp, symbol, price,
       LAG(price) OVER(PARTITION BY symbol ORDER BY timestamp) as prev_price
FROM trades
WHERE timestamp > dateadd('w', -1, now())
AND symbol = 'BTC-USDT' AND side = 'buy'
),
trends AS (
SELECT *,
  CASE WHEN price > prev_price THEN 1
       WHEN price < prev_price THEN 0 ELSE NULL END AS trend
FROM trade_and_previous
), prev_trends AS (
SELECT *,
      LAG(trend) IGNORE NULLS OVER(PARTITION BY SYMBOL ORDER BY TIMESTAMP) as prev_trend
FROM trends
)
SELECT timestamp, symbol, price, prev_price, price - prev_price as price_delta
from prev_trends where trend is not null and trend <> prev_trend limit -100;
"""
exec_sql(query)

(datetime.datetime(2025, 3, 31, 14, 45, 17, 938999), 'BTC-USDT', 83260.1, 83260.0, 0.10000000000582077)
(datetime.datetime(2025, 3, 31, 14, 45, 18, 602999), 'BTC-USDT', 83253.0, 83260.1, -7.100000000005821)
(datetime.datetime(2025, 3, 31, 14, 45, 22, 778000), 'BTC-USDT', 83201.1, 83200.1, 1.0)
(datetime.datetime(2025, 3, 31, 14, 45, 22, 778000), 'BTC-USDT', 83200.1, 83202.1, -2.0)
(datetime.datetime(2025, 3, 31, 14, 45, 22, 778000), 'BTC-USDT', 83201.1, 83200.1, 1.0)
(datetime.datetime(2025, 3, 31, 14, 45, 22, 898999), 'BTC-USDT', 83210.0, 83212.8, -2.8000000000029104)
(datetime.datetime(2025, 3, 31, 14, 45, 22, 898999), 'BTC-USDT', 83210.6, 83210.0, 0.6000000000058208)
(datetime.datetime(2025, 3, 31, 14, 45, 26, 637000), 'BTC-USDT', 83200.1, 83216.2, -16.09999999999127)
(datetime.datetime(2025, 3, 31, 14, 45, 27, 308999), 'BTC-USDT', 83194.1, 83191.1, 3.0)
(datetime.datetime(2025, 3, 31, 14, 45, 27, 308999), 'BTC-USDT', 83191.1, 83195.8, -4.69999999999709)
(datetime.datetime(2025, 3, 